# Russian Synodal Bible (1885)

## Import

### Libraries

In [1]:
import os
from itertools import chain
from backend import *
import matplotlib
import string

### Definitions

In [2]:
bibleTXT = '../texts/bible/sinodalnyi-perevod.txt' 
booksJSON = './proc/booksDict.json'
bibleJSON = '../texts/bible/bible.json'
bibleIdJSON = '../texts/bible/bibleID.json'
bibleXML = '../texts/bible/bible.xml'
bibFrazyTXT = '../texts/bible/Dubrovina_Slovar_Bibleyskikh_Frazeologizmov.txt'

bibleOHCO = ['test', 'book', 'chap', 'verse']
tokenCols = ['p_id', 'start', 'stop', 'text', 'token_id', 'head_id', 'rel', 'pos', 'lemma', 'anim', 'aspect', 'case', 'degree', 'gender', 'mood', 'number', 'person', 'tense', 'verb_form', 'voice']

chap_lines_re = '^===\s(\d{1,3})\s===$'
book_lines_re = '^==\s(.+)\s==$'
matt_name = 'От Матфея святое благовествование'

In [3]:
with open(booksJSON) as json_file: 
    booksDict = json.load(json_file)

## Pre-Processing

### Import Text into DF

In [4]:
with open(bibleTXT, 'r', encoding='windows-1251') as f: 
    bibleText = f.readlines()

bibliiaDf = pd.DataFrame(bibleText).rename(columns={0:'text'}).dropna()
bibliiaDf

text
0                                                     \n
1                                          == Бытие ==\n
2                                                     \n
3                                            === 1 ===\n
4                                                     \n
...                                                  ...
41374  17 И Дух и невеста говорят: прииди! И слышавши...
41375  18 И я также свидетельствую всякому слышащему ...
41376  19 и если кто отнимет что от слов книги пророч...
41377  20 Свидетельствующий сие говорит: ей, гряду ск...
41378  21 Благодать Господа нашего Иисуса Христа со в...

[41379 rows x 1 columns]

### Tidy Up

In [5]:
# remove blank lines and select puncutation, keeping only header & clean text lines
bibliiaDf.loc[:,'text'] = bibliiaDf.loc[:,'text'].str.replace(r'\n|^\s$', '')

#unwanted_parts = bibliiaDf.loc[bibliiaDf.text.str.contains('Предисловие|Примечания')].index.tolist() + bibliiaDf.loc[bibliiaDf.text.str.contains('^[^\d|^=]')].index.tolist() + [x for x in range(21483,21490)] + [x for x in range(16571,16577)]

# concat list of unwanted sections' indices
get_rid = chain(range(13259,13261), range(15172,15175), range(16571,16578), range(21483,21491))

# drop notes section from Book of Job
bibliiaDf = bibliiaDf.drop(index=[x for x in get_rid])

# rename foreword section for Esther and Wisdom of Jesus to match chapter style
#bibliiaDf.loc[:,'text'] = bibliiaDf.loc[:,'text'].str.replace('=== Предисловие ===', '=== 0 ===')

# remove various errata and notes marks
bibliiaDf.loc[:,'text'] = bibliiaDf.loc[:,'text'].str.replace('\]|\[|_|-|', '')
bibliiaDf = bibliiaDf.loc[bibliiaDf.text != '']#.reset_index().drop(columns="index")

bibliiaDf

text
0                                                     \n
1                                          == Бытие ==\n
2                                                     \n
3                                            === 1 ===\n
4                                                     \n
...                                                  ...
41374  17 И Дух и невеста говорят: прииди! И слышавши...
41375  18 И я также свидетельствую всякому слышащему ...
41376  19 и если кто отнимет что от слов книги пророч...
41377  20 Свидетельствующий сие говорит: ей, гряду ск...
41378  21 Благодать Господа нашего Иисуса Христа со в...

[41359 rows x 1 columns]

In [6]:
#bibliiaDf.loc[13259:13260] # MOLITVA and gospodi vsederzhiteliu
#bibliiaDf.loc[15172:15174] # predislovie for Esfira
#bibliiaDf.loc[16571:16577] # notes for Job
#bibliiaDf.loc[21483:21490] # предисловие for WisdJes

### Find Parts

In [7]:
# find df rows containing all the book and chapter title lines 
# as well as the OT/NT split on the 1st page of Matthew
chap_lines = bibliiaDf.loc[bibliiaDf.text.str.contains(chap_lines_re)].index
book_lines = bibliiaDf.loc[bibliiaDf.text.str.contains(book_lines_re)].index
test_line = bibliiaDf.loc[bibliiaDf.text.str.contains(matt_name)].index

# combine the title lines for extraction later
title_lines = test_line.append([chap_lines, book_lines]).sort_values()

/tmp/ipykernel_5707/2439614081.py:3: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  chap_lines = bibliiaDf.loc[bibliiaDf.text.str.contains(chap_lines_re)].index
/tmp/ipykernel_5707/2439614081.py:4: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  book_lines = bibliiaDf.loc[bibliiaDf.text.str.contains(book_lines_re)].index


### Assign OHCO Labels

In [8]:
bibliiaDf.text.str.split(pat=' ', n=0)

0                                                     [\n]
1                                        [==, Бытие, ==\n]
2                                                     [\n]
3                                          [===, 1, ===\n]
4                                                     [\n]
                               ...                        
41374    [17, И, Дух, и, невеста, говорят:, прииди!, И,...
41375    [18, И, я, также, свидетельствую, всякому, слы...
41376    [19, и, если, кто, отнимет, что, от, слов, кни...
41377    [20, Свидетельствующий, сие, говорит:, ей,, гр...
41378    [21, Благодать, Господа, нашего, Иисуса, Христ...
Name: text, Length: 41359, dtype: object

In [9]:
bibliiaDf

text
0                                                     \n
1                                          == Бытие ==\n
2                                                     \n
3                                            === 1 ===\n
4                                                     \n
...                                                  ...
41374  17 И Дух и невеста говорят: прииди! И слышавши...
41375  18 И я также свидетельствую всякому слышащему ...
41376  19 и если кто отнимет что от слов книги пророч...
41377  20 Свидетельствующий сие говорит: ей, гряду ск...
41378  21 Благодать Господа нашего Иисуса Христа со в...

[41359 rows x 1 columns]

In [10]:
# ['test']
bibliiaDf[bibleOHCO[0]] = np.where(bibliiaDf.index<test_line[0], 1, 2)
# ['book']
bibliiaDf[bibleOHCO[1]] = bibliiaDf.loc[book_lines].text.str.extract(book_lines_re)
# ['chap']
bibliiaDf[bibleOHCO[2]] = bibliiaDf.loc[chap_lines].text.str.extract(chap_lines_re)
# ['verse'] by splitting verse num at beginning from text in current verse lines
bibliiaDf[[bibleOHCO[3], 'text']] = bibliiaDf.text.str.split(' ', n=1, expand=True)
bibliiaDf

text  test   book chap  \
0                                                   None     1    NaN  NaN   
1                                             Бытие ==\n     1  Бытие  NaN   
2                                                   None     1    NaN  NaN   
3                                                1 ===\n     1    NaN    1   
4                                                   None     1    NaN  NaN   
...                                                  ...   ...    ...  ...   
41374  И Дух и невеста говорят: прииди! И слышавший д...     2    NaN  NaN   
41375  И я также свидетельствую всякому слышащему сло...     2    NaN  NaN   
41376  и если кто отнимет что от слов книги пророчест...     2    NaN  NaN   
41377  Свидетельствующий сие говорит: ей, гряду скоро...     2    NaN  NaN   
41378  Благодать Господа нашего Иисуса Христа со всем...     2    NaN  NaN   

      verse  
0        \n  
1        ==  
2        \n  
3       ===  
4        \n  
...     ...  
41374    17  
41375    18  
41376    19  
41377    20  
41378    21  

[41359 rows x 5 columns]

In [11]:
# ['test']
#bibliiaDf[bibleOHCO[0]] = np.where(bibliiaDf.index<test_line[0], 1, 2)
# ['book']
#bibliiaDf[bibleOHCO[1]] = bibliiaDf.loc[book_lines].text.str.extract(book_lines_re)
# ['chap']
#bibliiaDf[bibleOHCO[2]] = bibliiaDf.loc[chap_lines].text.str.extract(chap_lines_re)
# ['verse'] by splitting verse num at beginning from text in current verse lines
#bibliiaDf[[bibleOHCO[3],'text']] = bibliiaDf.text.str.split(pat=' ', n=1).iloc[:, [0, 1]]

# fill in book and chapter titles to cells below them
bibliiaDf[bibleOHCO[1:3]] = bibliiaDf[['book','chap']].ffill()

# transfer book numbers onto book titles
#bibliiaDf[bibleOHCO[1]] = bibliiaDf[bibleOHCO[1]].map(dict([(y,x) for (x,y) in enumerate(bibliiaDf.book.unique(), start=1)]))

# drop title lines and reset index to give verse id num 
bibliiaDf = bibliiaDf.drop(title_lines, axis=0).reset_index()#.set_index(bibleOHCO)
bibliiaDf.index = range(1,len(bibliiaDf)+1)
bibliiaDf.index.name = 'v_id'

# reorder columns
bibliiaDf = bibliiaDf[['test', 'book', 'chap', 'verse', 'text']]
bibliiaDf

test                                 book chap verse  \
v_id                                                          
1         1                                  NaN  NaN    \n   
2         1                                Бытие  NaN    \n   
3         1                                Бытие    1    \n   
4         1                                Бытие    1     1   
5         1                                Бытие    1     2   
...     ...                                  ...  ...   ...   
39917     2  Откровение святого Иоанна Богослова   22    17   
39918     2  Откровение святого Иоанна Богослова   22    18   
39919     2  Откровение святого Иоанна Богослова   22    19   
39920     2  Откровение святого Иоанна Богослова   22    20   
39921     2  Откровение святого Иоанна Богослова   22    21   

                                                    text  
v_id                                                      
1                                                   None  
2                                                   None  
3                                                   None  
4                  В начале сотворил Бог небо и землю.\n  
5      Земля же была безвидна и пуста, и тьма над без...  
...                                                  ...  
39917  И Дух и невеста говорят: прииди! И слышавший д...  
39918  И я также свидетельствую всякому слышащему сло...  
39919  и если кто отнимет что от слов книги пророчест...  
39920  Свидетельствующий сие говорит: ей, гряду скоро...  
39921  Благодать Господа нашего Иисуса Христа со всем...  

[39921 rows x 5 columns]

### Swap Russian Book Name for English Equivalent

In [12]:
booksDict.keys()
total_books = 0
for book in booksDict.keys():
    total_books += sum(booksDict[book]['chap_verse'].values())
print(total_books)

37086


In [ ]:
book_nums = [(x,y) for x,y in enumerate(bibliiaDf.book.unique())][1:]
bibliiaDf['book_en'] = [booksDict[str(x)]['en_name'] for x,y in book_nums for name in bibliiaDf.book if y == name]

In [14]:
bibliiaDf.loc[~bibliiaDf.isnull().any(axis=1)].reset_index()

v_id  test                                 book chap verse  \
0          4     1                                Бытие    1     1   
1          5     1                                Бытие    1     2   
2          6     1                                Бытие    1     3   
3          7     1                                Бытие    1     4   
4          8     1                                Бытие    1     5   
...      ...   ...                                  ...  ...   ...   
37089  39917     2  Откровение святого Иоанна Богослова   22    17   
37090  39918     2  Откровение святого Иоанна Богослова   22    18   
37091  39919     2  Откровение святого Иоанна Богослова   22    19   
37092  39920     2  Откровение святого Иоанна Богослова   22    20   
37093  39921     2  Откровение святого Иоанна Богослова   22    21   

                                                    text  
0                  В начале сотворил Бог небо и землю.\n  
1      Земля же была безвидна и пуста, и тьма над без...  
2            И сказал Бог: да будет свет. И стал свет.\n  
3      И увидел Бог свет, что он хорош, и отделил Бог...  
4      И назвал Бог свет днем, а тьму ночью. И был ве...  
...                                                  ...  
37089  И Дух и невеста говорят: прииди! И слышавший д...  
37090  И я также свидетельствую всякому слышащему сло...  
37091  и если кто отнимет что от слов книги пророчест...  
37092  Свидетельствующий сие говорит: ей, гряду скоро...  
37093  Благодать Господа нашего Иисуса Христа со всем...  

[37094 rows x 6 columns]

### Export to JSON

In [15]:
bibliiaDf.to_json(bibleJSON, orient='index')

## Processing

### OHCO DFs

#### Dictionaries for testament and book IDs

In [16]:
#testsDict = dict(enumerate(bibliiaDf.test.unique()))
testsDict = dict([(value, key) for key, value in dict(enumerate(bibliiaDf.test.unique())).items()])
booksDict = dict([(value, key) for key, value in dict(enumerate(bibliiaDf.book.unique())).items()])

#### Testaments

In [ ]:
# make df of testament texts

TestsDf = pd.DataFrame([(x, ' '.join(y)) for (x,y) in bibliiaDf.\
    groupby('test', sort=False).text], columns=['test', 'text']).\
        set_index(np.arange(1,len(bibliiaDf.test.unique())+1))
TestsDf.index.name = 't_id'
TestsDf 

#### Books

In [ ]:
## make Df of book texts

BooksDf = pd.DataFrame([(x, ' '.join(y)) for (x,y) in bibliiaDf.\
    groupby('book', sort=False).text], columns=['book', 'text'])\
    .set_index(np.arange(1,len(bibliiaDf.book.unique())+1))
BooksDf.index.name = 'b_id'

BooksDf 

#### Chapters

In [19]:
# grab book name and chapter number from main df
ChapsDf = pd.DataFrame([(x, ' '.join(y)) for (x,y) in bibliiaDf.groupby(bibleOHCO[1:3], sort=False).text], columns=[('book', 'chap'), 'text'])
ChapsDf[['book','chap']] = pd.DataFrame(list(ChapsDf[('book', 'chap')]), index=ChapsDf.index, columns=bibleOHCO[1:3])
del ChapsDf[('book', 'chap')]
#ChapsDf = ChapsDf.replace({"book": booksDict}).sort_values(by=bibleOHCO[1:3], ascending=[True, True])

ChapsDf = ChapsDf.reset_index().drop(['index'], axis=1).set_index(np.arange(1,len(ChapsDf)+1))
ChapsDf.index.name = 'c_id'

#ChapsDf = ChapsDf.replace({"book":dict(enumerate(bibliiaDf.book.unique()))})
#ChapsDf = ChapsDf.reset_index().set_index(bibleOHCO[:3])

ChapsDf

TypeError: sequence item 0: expected str instance, NoneType found

In [20]:
# make t_id and b_id columns with TestsDf and BooksDf IDs respectively
bibliiaDf['t_id'] = bibliiaDf['test'].map(TestsDf.reset_index().set_index('test')['t_id'])
bibliiaDf['b_id'] = bibliiaDf['book'].map(BooksDf.reset_index().set_index('book')['b_id'])

# merge existing bibliiaDf with Chapsdf for c_id column (because it's based on multiple matching columns)
bibliiaDf = pd.merge(bibliiaDf, ChapsDf.reset_index()[['book', 'chap', 'c_id']], on=['book', 'chap'], how='left')

# remake index
bibliiaDf = bibliiaDf.reset_index().drop(['index'], axis=1).set_index(np.arange(1,len(bibliiaDf)+1))
bibliiaDf.index.name = 'v_id'

bibliiaDf

NameError: name 'TestsDf' is not defined

In [ ]:
bibliiaDf.to_json(bibleIdJSON, orient='index')

### Make XML

In [4]:
bibliiaDf = pd.read_json(bibleIdJSON, orient='index')

In [5]:
bibliiaDf#.rename(columns={'book':'book_ru'})

test                                 book  chap  verse  \
1         1                                Бытие     1      1   
2         1                                Бытие     1      2   
3         1                                Бытие     1      3   
4         1                                Бытие     1      4   
5         1                                Бытие     1      5   
...     ...                                  ...   ...    ...   
37082     2  Откровение святого Иоанна Богослова    22     17   
37083     2  Откровение святого Иоанна Богослова    22     18   
37084     2  Откровение святого Иоанна Богослова    22     19   
37085     2  Откровение святого Иоанна Богослова    22     20   
37086     2  Откровение святого Иоанна Богослова    22     21   

                                                    text  t_id  b_id  c_id_x  \
1                    В начале сотворил Бог небо и землю.     1     1       1   
2      Земля же была безвидна и пуста, и тьма над без...     1     1       1   
3              И сказал Бог: да будет свет. И стал свет.     1     1       1   
4      И увидел Бог свет, что он хорош, и отделил Бог...     1     1       1   
5      И назвал Бог свет днем, а тьму ночью. И был ве...     1     1       1   
...                                                  ...   ...   ...     ...   
37082  И Дух и невеста говорят: прииди! И слышавший д...     2    77    1361   
37083  И я также свидетельствую всякому слышащему сло...     2    77    1361   
37084  и если кто отнимет что от слов книги пророчест...     2    77    1361   
37085  Свидетельствующий сие говорит: ей, гряду скоро...     2    77    1361   
37086  Благодать Господа нашего Иисуса Христа со всем...     2    77    1361   

                  book_en  c_id_y  
1                 Genesis       1  
2                 Genesis       1  
3                 Genesis       1  
4                 Genesis       1  
5                 Genesis       1  
...                   ...     ...  
37082  Book of Revelation    1361  
37083  Book of Revelation    1361  
37084  Book of Revelation    1361  
37085  Book of Revelation    1361  
37086  Book of Revelation    1361  

[37086 rows x 10 columns]

In [7]:
bookRefDict = {}
for book in booksDict.items():
    cleanDict = {int(book[0]):book[1]}
    cleanDict[int(book[0])]['chap_verse'] = bibliiaDf.loc[bibliiaDf.b_id == int(book[0])].groupby('chap').max().to_dict()['verse']
    #print(verseDict)
    #cleanDict.update(verseDict)
    #print(cleanDict)
    bookRefDict.update(cleanDict)
#bookRefDict

In [24]:
with open('../site/data/booksDict.json', "w") as outfile:
    json.dump(bookRefDict, outfile)
    #json.dump('../site/data/booksDict.json', outfile)

In [ ]:
root = etree.Element("bible")
print(root.tag)
t = b = c = v = 1
#TestList = [x for x in bibliiaDf.test.unique()]
#for test in range(len(TestList)): 
#    root.append(etree.Element("t", n=str(t), name=TestList[test]))
BookList = list(bibliiaDf.book.unique())
for book in range(len(BookList)): 
    root.append(etree.Element("b", n=str(b), name_ru=BookList[book], name_en=bibliiaDf.loc[bibliiaDf.book==BookList[book]].book_en.unique()[0]))
    ChapList = list(bibliiaDf.loc[bibliiaDf['book'] == BookList[book]].chap.unique())
    for chap in range(len(ChapList)): 
        root[book].append(etree.Element("c", n=str(c), name=str(chap+1)))
        VerseList = list(bibliiaDf.loc[(bibliiaDf['book'] == BookList[book]) & (bibliiaDf['chap'] == ChapList[chap])].index)
        for verse in range(len(VerseList)): 
            root[book][chap].append(etree.Element("v", n=str(v), name=str(verse+1)))
            verse_text = bibliiaDf.loc[v].text
            root[book][chap][verse].text = verse_text
            v+=1
        c+=1
    b+=1
#t+=1
#print(etree.tostring(root, pretty_print=True, xml_declaration=True))
etree.ElementTree(root).write(bibleXML, pretty_print=True, xml_declaration=True, encoding='windows-1251')

## Token DFs

In [6]:
#bibliiaDf = pd.read_json(bibleJSON, orient='index')
#bibliiaDf.index.name = 'v_id'
BibTextDf = bibliiaDf[['text']]
BibLibDf = bibliiaDf[bibleOHCO]
bibliiaDf

test                                 book  chap  verse  \
1         1                                Бытие     1      1   
2         1                                Бытие     1      2   
3         1                                Бытие     1      3   
4         1                                Бытие     1      4   
5         1                                Бытие     1      5   
...     ...                                  ...   ...    ...   
37082     2  Откровение святого Иоанна Богослова    22     17   
37083     2  Откровение святого Иоанна Богослова    22     18   
37084     2  Откровение святого Иоанна Богослова    22     19   
37085     2  Откровение святого Иоанна Богослова    22     20   
37086     2  Откровение святого Иоанна Богослова    22     21   

                                                    text  t_id  b_id  c_id_x  \
1                    В начале сотворил Бог небо и землю.     1     1       1   
2      Земля же была безвидна и пуста, и тьма над без...     1     1       1   
3              И сказал Бог: да будет свет. И стал свет.     1     1       1   
4      И увидел Бог свет, что он хорош, и отделил Бог...     1     1       1   
5      И назвал Бог свет днем, а тьму ночью. И был ве...     1     1       1   
...                                                  ...   ...   ...     ...   
37082  И Дух и невеста говорят: прииди! И слышавший д...     2    77    1361   
37083  И я также свидетельствую всякому слышащему сло...     2    77    1361   
37084  и если кто отнимет что от слов книги пророчест...     2    77    1361   
37085  Свидетельствующий сие говорит: ей, гряду скоро...     2    77    1361   
37086  Благодать Господа нашего Иисуса Христа со всем...     2    77    1361   

                  book_en  c_id_y  
1                 Genesis       1  
2                 Genesis       1  
3                 Genesis       1  
4                 Genesis       1  
5                 Genesis       1  
...                   ...     ...  
37082  Book of Revelation    1361  
37083  Book of Revelation    1361  
37084  Book of Revelation    1361  
37085  Book of Revelation    1361  
37086  Book of Revelation    1361  

[37086 rows x 10 columns]

In [ ]:
BibTextDf

In [ ]:
%%time
VerseTokenDf = nat_parse(BibTextDf)

Text DF Index id:   0%|          | 0/37086 [00:00<?, ?it/s]

Token id:   0%|          | 0/7 [00:00<?, ?it/s]

Token id:   0%|          | 0/16 [00:00<?, ?it/s]

Token id:   0%|          | 0/9 [00:00<?, ?it/s]

Token id:   0%|          | 0/13 [00:00<?, ?it/s]

...

Token id:   0%|          | 0/26 [00:00<?, ?it/s]

Token id:   0%|          | 0/27 [00:00<?, ?it/s]

Token id:   0%|          | 0/14 [00:00<?, ?it/s]

Token id:   0%|          | 0/20 [00:00<?, ?it/s]

Token id:   0%|          | 0/16 [00:00<?, ?it/s]

In [ ]:
VerseTokenDf

In [28]:
VerseTokenDf.to_pickle('./proc/BibleTokenDf.pkl')

In [12]:
VerseTokenDf = pd.read_pickle('./proc/BibleTokenDf.pkl')
VerseTokenDf['stopword'] = ~VerseTokenDf.loc[:, tokenCols[9:]].any(axis=1)
VerseTokenDfIdx = pd.Index(range(1, (VerseTokenDf.shape[0]+1)), name='id')
VerseTokenDf.index = VerseTokenDfIdx# = TokenDf.set_index(['p_id', 'token_id'])

In [13]:
VerseTokenDf

p_id start stop      text token_id head_id        rel    pos  \
id                                                                      
1           1     0    1         В      1_1     1_2       case    ADP   
2           1     2    8    начале      1_2     1_3        obl   NOUN   
3           1     9   17  сотворил      1_3     1_0       root   VERB   
4           1    18   21       Бог      1_4     1_3      nsubj  PROPN   
5           1    22   26      небо      1_5     1_3        obj   NOUN   
...       ...   ...  ...       ...      ...     ...        ...    ...   
675064  37086    32   38    Христа      1_5     1_4  flat:name  PROPN   
675065  37086    39   41        со      1_6     1_8       case    ADP   
675066  37086    42   47     всеми      1_7     1_8        det    DET   
675067  37086    48   52      вами      1_8     1_4       nmod   PRON   
675068  37086    54   59     Аминь      2_1     2_0       root  PROPN   

            lemma  anim  ...  case degree gender  mood number person tense  \
id                       ...                                                 
1               в  None  ...  None   None   None  None   None   None  None   
2          начало  Inan  ...   Loc   None   Neut  None   Sing   None  None   
3       сотворить  None  ...  None   None   Masc   Ind   Sing   None  Past   
4             бог  Anim  ...   Nom   None   Masc  None   Sing   None  None   
5            небо  Inan  ...   Acc   None   Neut  None   Sing   None  None   
...           ...   ...  ...   ...    ...    ...   ...    ...    ...   ...   
675064    христос  Anim  ...   Gen   None   Masc  None   Sing   None  None   
675065          с  None  ...  None   None   None  None   None   None  None   
675066       весь  None  ...   Ins   None   None  None   Plur   None  None   
675067         вы  None  ...   Ins   None   None  None   Plur      2  None   
675068      аминь  Inan  ...   Gen   None    Fem  None   Sing   None  None   

       verb_form voice stopword  
id                               
1           None  None     True  
2           None  None    False  
3            Fin   Act    False  
4           None  None    False  
5           None  None    False  
...          ...   ...      ...  
675064      None  None    False  
675065      None  None     True  
675066      None  None    False  
675067      None  None    False  
675068      None  None    False  

[675068 rows x 21 columns]

In [14]:
# stopword counts

VerseTokenDf.loc[TokenDf.stopword == True].lemma.value_counts()[:25]

lemma
и        32725
в         9877
не        5592
на        4877
с         3427
он        3120
к         2776
из        2746
что       2673
от        2570
они       2152
я         1914
быть      1891
как       1798
по        1781
а         1715
у         1650
ибо       1406
же        1392
для       1347
за        1332
ты        1319
но        1259
когда     1215
вот       1059
Name: count, dtype: int64

In [15]:
VerseTokenDf.loc[TokenDf[tokenCols[9]] == 'Anim'].lemma.value_counts().to_frame()

count
lemma              
и              3675
господь        3526
сын            3080
бог            1924
царь           1782
...             ...
возвратишься      1
едемский          1
омега             1
филадельфия       1
смирнский         1

[8564 rows x 1 columns]

In [16]:
GetRankDf(VerseTokenDf)#.plot(x='rank')

count   rank
lemma                    
он           19628      1
они          12309      2
быть         10827      3
я            10744      4
ты            7837      5
...            ...    ...
вытрут           1  20774
неприятелям      1  20775
смирнский        1  20776
сатанинское      1  20777
ввергать         1  20778

[20778 rows x 2 columns]

In [17]:
GetRankDf(VerseTokenDf, 'pos')

count  rank
pos                
NOUN   146734     1
VERB   107895     2
PRON    78370     3
PROPN   55154     4
ADJ     35241     5
DET     31903     6
ADV     21255     7
AUX     10129     8
NUM      7025     9
SCONJ    1630    10

In [18]:
VocabDf = VerseTokenDf.loc[VerseTokenDf.stopword != True].lemma.value_counts().to_frame().reset_index()
VocabDf.columns = ['lemma', 'count']
VocabDf.index = VocabDf.index.map(lambda x: x + 1).rename('rank')
VocabDf.iloc[:25]#.plot(x='rank')

lemma  count
rank                 
1           он  19628
2          они  12309
3         быть  10827
4            я  10744
5           ты   7837
6      господь   7091
7         весь   6971
8         свой   6037
9         твой   5947
10     сказать   5844
11         сын   5422
12     который   5414
13         мой   5128
14          вы   4675
15         бог   4419
16         тот   4342
17    говорить   3732
18         она   3405
19       земля   3297
20       народ   3253
21        царь   3225
22          мы   3139
23        день   2782
24     человек   2349
25         это   2187

In [19]:
bibliiaType = {'test':str, 'book':str, 'chap':int, 'verse':int}
bibliiaDf = pd.read_json(bibleJSON, orient='index', dtype=bibliiaType)
bibliiaDf.index.name = 'p_id'
#bibliiaDf.verse = bibliiaDf.verse.astype(int)
p_idDict = bibliiaDf.drop('text', axis=1).to_dict(orient='index')
bibliiaDf

test                                 book  chap verse  \
p_id                                                          
1        1                                 None  None    \n   
2        1                                Бытие  None    \n   
3        1                                Бытие     1    \n   
4        1                                Бытие     1     1   
5        1                                Бытие     1     2   
...    ...                                  ...   ...   ...   
39917    2  Откровение святого Иоанна Богослова    22    17   
39918    2  Откровение святого Иоанна Богослова    22    18   
39919    2  Откровение святого Иоанна Богослова    22    19   
39920    2  Откровение святого Иоанна Богослова    22    20   
39921    2  Откровение святого Иоанна Богослова    22    21   

                                                    text  
p_id                                                      
1                                                   None  
2                                                   None  
3                                                   None  
4                  В начале сотворил Бог небо и землю.\n  
5      Земля же была безвидна и пуста, и тьма над без...  
...                                                  ...  
39917  И Дух и невеста говорят: прииди! И слышавший д...  
39918  И я также свидетельствую всякому слышащему сло...  
39919  и если кто отнимет что от слов книги пророчест...  
39920  Свидетельствующий сие говорит: ей, гряду скоро...  
39921  Благодать Господа нашего Иисуса Христа со всем...  

[39921 rows x 5 columns]

In [ ]:
# dictionary with verse lines in format 
# {book: {0: first_line, last_line}, {chap_num: (first_chap_line, last_chap_line)}}
PartLineNumsDict = {}
for test_name in bibliiaDf.test.unique():
    t_min = bibliiaDf.loc[bibliiaDf['test'] == test_name].reset_index().p_id.min()
    t_max = bibliiaDf.loc[bibliiaDf['test'] == test_name].reset_index().p_id.max()
    print(f"{test_name}: {t_min} - {t_max}")
    for book_name in bibliiaDf.book.unique():
        b_min = bibliiaDf.loc[bibliiaDf['book'] == book_name].reset_index().p_id.min()
        b_max = bibliiaDf.loc[bibliiaDf['book'] == book_name].reset_index().p_id.max()
        PartLineNumsDict.update({book_name: {0: (b_min, b_max)}})
        #print(f"{book_name}: {b_min} - {b_max}")
        for chap_name in bibliiaDf.loc[bibliiaDf['book'] == book_name].chap.unique():
            c_min = bibliiaDf.loc[(bibliiaDf['book'] == book_name) & (bibliiaDf['chap'] == chap_name)].reset_index().p_id.min()
            c_max = bibliiaDf.loc[(bibliiaDf['book'] == book_name) & (bibliiaDf['chap'] == chap_name)].reset_index().p_id.max()
            PartLineNumsDict[book_name][chap_name] = (c_min, c_max)
            #    print(f"{chap_name}: {c_min} - {c_max}")
#print(PartLineNumsDict)

In [ ]:
TokenDf.loc[(TokenDf['p_id'] >= count_start) & (TokenDf['p_id'] <= count_stop)].lemma.value_counts()

In [ ]:
[x for x in PartLineNumsDict]

### Manual TF-IDF

In [ ]:
# TF-IDF

TfidfDf = TokenDf.reindex(columns=['text', 'lemma', 'tfidf_bible', 'tfidf_book', 'tfidf_chap'])
#vocab = TokenDf.loc[TokenDf['p_id'] <= 10, 'lemma'].unique().tolist()

def getTFIDF(count_start=0, count_stop=(TokenDf.shape[0]+1)):

    return TFIDF

count_start = 0
count_stop = (TokenDf.shape[0]+1)

TfidfCountDf = TokenDf.loc[(TokenDf['p_id'] >= count_start) & (TokenDf['p_id'] <= count_stop)][['p_id', 'lemma']]
VocabCountDict = TfidfCountDf.value_counts('lemma').to_dict()

total_words = sum(VocabCountDict.values())
num_docs = TfidfCountDf.p_id.unique().size
    
for lemma in VocabCountDict.keys(): 

    instances = VocabCountDict.get(lemma)
    docsw_word = TfidfCountDf.loc[TfidfCountDf['lemma'] == lemma].p_id.unique().size

    TF = instances / total_words
    IDF = num_docs / docsw_word
    TFIDF = TF * IDF

    TfidfDf['tfidf_bible'].loc[TfidfDf['lemma'] == lemma] = TFIDF

#TfidfDf['tfidf_bible'] = TokenDf

# PartLineNumsDict = {book: {0: first_line, last_line}, {chap_num: (first_chap_line, last_chap_line)}}

TfidfDf

In [ ]:
TfidfDf.to_pickle('./proc/TfidfDf.pkl')

In [30]:
TfidfDf = pd.read_pickle('./proc/TfidfDf.pkl')
TfidfDf

text      lemma  tfidf_bible  tfidf_book  tfidf_chap
id                                                              
1              В          в     0.075158         NaN         NaN
2         начале     начало     0.055755         NaN         NaN
3       сотворил  сотворить     0.057942         NaN         NaN
4            Бог        бог     0.063870         NaN         NaN
5           небо       небо     0.058612         NaN         NaN
...          ...        ...          ...         ...         ...
676262    Христа    христос     0.058178         NaN         NaN
676263        со          с     0.066290         NaN         NaN
676264     всеми       весь     0.067202         NaN         NaN
676265      вами         вы     0.080405         NaN         NaN
676266     Аминь      аминь     0.061808         NaN         NaN

[676266 rows x 5 columns]

In [42]:
len(TokenDf.p_id.unique())

37102

In [31]:
GetRankDf(TokenDf)

count   rank
lemma                 
он        19656      1
они       12325      2
быть      10839      3
я         10762      4
ты         7851      5
...         ...    ...
паша          1  20821
кисточка      1  20822
лживость      1  20823
горьки        1  20824
точила        1  20825

[20825 rows x 2 columns]

In [45]:
TfidfDf.sort_values('tfidf_bible', ascending=False).lemma.unique()[:20]

array(['глядели', 'скопец', 'воспрянь', 'окропили', '=', 'элнафан',
       'трехлетний', 'любодейный', 'хусарсафема', 'отвергаться', 'и',
       'связка', 'почитаю', 'оклад', 'споспешествуй', 'юпитер',
       'возливальница', 'силомский', 'ефиоплянка', 'шеломоф'],
      dtype=object)

## NER-supplemented Bible text

pronominal references swapped with names

## Bible Phrase Dictionary

In [20]:
with open(bibFrazyTXT) as bibleFrazy: 
    bibleFrazyLines = bibleFrazy.readlines()

In [21]:
BibleFrazyDf = pd.DataFrame(bibleFrazyLines).rename(columns={0:'fraza'})
BibleFrazyDf.loc[:,'fraza'] = BibleFrazyDf.loc[:,'fraza'].apply(lambda x: x.strip().strip('\n').translate(str.maketrans('', '', string.punctuation)))
BibleFrazyDf = BibleFrazyDf.loc[BibleFrazyDf.fraza != '']

In [22]:
frazyList = BibleFrazyDf.loc[30189:].fraza.to_list()
FrazyDf = pd.DataFrame(data=frazyList).rename(columns={0:'fraza'})
FrazyDf.index.name = 'f_id'
FrazyDf

fraza
f_id                                                   
0     Агнец Божий непорочный как будто как будто сло...
1                                        Адамова голова
2                                        Адамово яблоко
3                                  Адамовы веки времена
4                                         Адамовы слёзы
...                                                 ...
535                            Что посеешь то и пожнёшь
536   Юдоль плача печали скорби бед плачевная земная...
537                               Явление Христа народу
538    Язык прилип прильпе  устар к гортани у кого чьей
539                             Яко аки как тать в нощи

[540 rows x 1 columns]

In [23]:
%%capture
FrazyDf = nat_parse(FrazyDf, textCol='fraza')

In [24]:
FrazyDf['stopword'] = ~FrazyDf.loc[:, tokenCols[9:]].any(axis=1)
#FrazyDf = FrazyDf.set_index('p_id', 'token_id')
FrazyDf

p_id start stop        text token_id head_id    rel    pos       lemma  \
0     0     0    5       Агнец      1_1     1_3  nsubj  PROPN       агнец   
1     0     6   11       Божий      1_2     1_1    det    ADJ       божий   
2     0    12   22  непорочный      1_3     1_0   root   VERB  непорочный   
3     0    23   26         как      1_4    1_10   mark  SCONJ         как   
4     0    27   32       будто      1_5     1_6  fixed   PART       будто   
..  ...   ...  ...         ...      ...     ...    ...    ...         ...   
1   539     4    7         аки      1_2     1_1    obj   NOUN         аки   
2   539     8   11         как      1_3     1_4   case  SCONJ         как   
3   539    12   16        тать      1_4     1_2    acl   NOUN        тать   
4   539    17   18           в      1_5     1_6   case    ADP           в   
5   539    19   23        нощи      1_6     1_4    obl   NOUN        нощь   

    anim  ...  case degree gender  mood number person tense verb_form voice  \
0   Anim  ...   Nom   None   Masc  None   Sing   None  None      None  None   
1   None  ...   Nom    Pos   Masc  None   Sing   None  None      None  None   
2   None  ...  None   None   Masc   Ind   Sing   None  Past       Fin   Mid   
3   None  ...  None   None   None  None   None   None  None      None  None   
4   None  ...  None   None   None  None   None   None  None      None  None   
..   ...  ...   ...    ...    ...   ...    ...    ...   ...       ...   ...   
1   Anim  ...   Nom   None   Masc  None   Sing   None  None      None  None   
2   None  ...  None   None   None  None   None   None  None      None  None   
3   Inan  ...   Nom   None   Masc  None   Sing   None  None      None  None   
4   None  ...  None   None   None  None   None   None  None      None  None   
5   Inan  ...   Loc   None   Masc  None   Sing   None  None      None  None   

   stopword  
0     False  
1     False  
2     False  
3      True  
4      True  
..      ...  
1     False  
2      True  
3     False  
4      True  
5     False  

[2668 rows x 21 columns]

In [25]:
for phrase_id in FrazyDf.p_id.unique().tolist():
   testPhrase = FrazyDf.loc[FrazyDf.p_id] 

KeyError: '[19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220, 221, 222, 223, 224, 225, 226, 227, 228, 229, 230, 231, 232,

In [ ]:
pos_lists = []
for x in range(0,(FrazyDf.p_id.max()+1)):
    pos_lists.append(FrazyDf.loc[(FrazyDf.p_id == x) & (FrazyDf.stopword == False)].lemma.unique())

In [ ]:
#bibliiaDf.loc[(bibliiaDf.test == 'N')]
bibliiaDf.loc[(bibliiaDf.book == 'Lk') & (bibliiaDf.chap == 10) & (bibliiaDf.verse == '42')].index

In [ ]:
bibliiaDf.loc[31412].text

In [ ]:
#phraseList = [x.tolist() for x in pos_lists]
for verse_id in range(31400,31450):
    print(f"verse_id: {verse_id}")
    testVerse = TokenDf.loc[(TokenDf.p_id == verse_id) & (TokenDf.stopword == False)].lemma.tolist()
    print(f"testVerse: {testVerse}")
    for phrase in pos_lists:
        print(f"phrase: {phrase}")
        i = 0
        for word in phrase:
            if word in testVerse:
                i+=1
        print(f"{verse_id} : {i} / {phrase.size}")

In [ ]:
TokenDf.loc[TokenDf.p_id == 31400]

In [ ]:
FrazyDf.loc[FrazyDf.p_id == 31400].lemma.tolist()

In [ ]:
testPhrase = FrazyDf.loc[FrazyDf.p_id == 22].lemma.unique()

In [ ]:
testVerse = TokenDf.loc[TokenDf.p_id == 31412].lemma.tolist()

In [ ]:
i = 0
print(testPhrase.tolist())
print(testVerse)
for x in testPhrase.tolist():
    if x in testVerse:
        i+=1
print(f"i = {i}")
if i == testPhrase.size:
    print("phrase in verse")

In [ ]:
for x in pos_lists[20:25]:
    print(x)
    for y in TokenDf.p_id:
        #print(TokenDf.loc[TokenDf.p_id == y].lemma.unique())
        #if x in TokenDf.loc[TokenDf.p_id == y].lemma.unique():
            #print(f"{x} in {y}")

In [ ]:
FrazyAbbrsDf = BibleFrazyDf.iloc[:105].fraza.str.split(' – ', expand=True).rename(columns={0:"abbr", 1:"fraza"})
FrazyAbbrsDf.loc[:,'abbr'] = FrazyAbbrsDf.loc[:,'abbr'].apply(lambda x: x.strip())
FrazyAbbrsDf.loc[:,'fraza'] = FrazyAbbrsDf.loc[:,'fraza'].apply(lambda x: x.strip())
FrazyAbbrsDict = FrazyAbbrsDf.set_index('abbr').to_dict().get('fraza')
FrazyAbbrsDict